In [ ]:
'''

Objective: compare and contrast binary, rule-based sentiment classifiers on labeled movie reviews

Classifiers:
    -VADER (Valence Aware Dictionary for sEntiment Reasoning)
        -Binary classifier
        -Created by human experts
        -Uses polarity scale -4 to 4 (>0 => positive, <0 => negative)
        -Built into Python nltk
        -Works well with emoticons, idioms, and slang
        -Algorithm + Lexicon combined
    -Sentiwordnet
        -A single word can have multiple meanings
        -A Wordnet creates a "net" for each word, tying it to its various meanings
        -Sentiwordnet builds off of a wordnet but instead ties polarities to each definition
    -These classifiers reduce the burden of creating our own systems to create context and derive sentiment

Data source: http://www.cs.cornell.edu/people/pabo/movie-review-data/

'''

In [9]:
'''
########################################################
 Test VADER's sentiment analyzer with a simple examples
########################################################
'''
# compound score = aggregate score of data sample
from nltk.sentiment import vader
sia = vader.SentimentIntensityAnalyzer()

# Effect of puncuation
print(sia.polarity_scores('What a terrible restaurant'))
print(sia.polarity_scores('What a terrible restaurant!'))
print(sia.polarity_scores('What a terrible restaurant!!'))

{'neg': 0.608, 'neu': 0.392, 'pos': 0.0, 'compound': -0.4767}
{'neg': 0.629, 'neu': 0.371, 'pos': 0.0, 'compound': -0.5255}
{'neg': 0.648, 'neu': 0.352, 'pos': 0.0, 'compound': -0.5696}


In [10]:
# Emoticons
print(sia.polarity_scores(':D'))
print(sia.polarity_scores(':/'))

{'neg': 0.0, 'neu': 0.0, 'pos': 1.0, 'compound': 0.5106}
{'neg': 1.0, 'neu': 0.0, 'pos': 0.0, 'compound': -0.34}


In [11]:
# Idioms
print(sia.polarity_scores('The cumin was the kiss of death'))

{'neg': 0.5, 'neu': 0.5, 'pos': 0.0, 'compound': -0.6124}


In [13]:
# Negation
print(sia.polarity_scores('The food was good!!'))
print(sia.polarity_scores('The food was not good!!'))
print(sia.polarity_scores('The food was not the worst!!'))

{'neg': 0.0, 'neu': 0.463, 'pos': 0.537, 'compound': 0.5399}
{'neg': 0.428, 'neu': 0.572, 'pos': 0.0, 'compound': -0.457}
{'neg': 0.0, 'neu': 0.563, 'pos': 0.437, 'compound': 0.5964}


In [14]:
# Capitalization
print(sia.polarity_scores('The food was good!!'))
print(sia.polarity_scores('The food was GOOD!!'))

{'neg': 0.0, 'neu': 0.463, 'pos': 0.537, 'compound': 0.5399}
{'neg': 0.0, 'neu': 0.416, 'pos': 0.584, 'compound': 0.639}


In [15]:
# Gusto words
print(sia.polarity_scores('The food was good!!'))
print(sia.polarity_scores('The food was SO good!!'))

{'neg': 0.0, 'neu': 0.463, 'pos': 0.537, 'compound': 0.5399}
{'neg': 0.0, 'neu': 0.47, 'pos': 0.53, 'compound': 0.6715}


In [17]:
# Contrast
# Emphasizes content after the word 'but'
print(sia.polarity_scores('I usually hate seafood, but I liked this'))

# This analysis fails because of how VADER processes 'and'
print(sia.polarity_scores('I usually hate seafood, and I liked this'))

{'neg': 0.234, 'neu': 0.398, 'pos': 0.368, 'compound': 0.3291}
{'neg': 0.352, 'neu': 0.381, 'pos': 0.267, 'compound': -0.2263}


In [22]:
'''
######################################################
 Test VADER's sentiment analyzer with a movie reviews
######################################################
'''
# Instantiate our sentiment analyzer
sia = vader.SentimentIntensityAnalyzer()

# Read in movie review data
positiveReviewsFileName = 'data/rt-polarity.pos'
negativeReviewsFileName = 'data/rt-polarity.neg'

with open(positiveReviewsFileName) as f:
    positiveReviews = f.readlines()
    
with open(negativeReviewsFileName) as f:
    negativeReviews = f.readlines()

In [62]:
# Define functions that will be used for the analysis of this dataset

def vaderSentiment(review):
    '''
    Get compound polarity score for a review
    '''
    return sia.polarity_scores(review)['compound']

def getReviewSentiments(sentimentCalculator):
    '''
    Get compound sentiment value for each negative and positive review.
    return dictionary of positive and negative review results
    
    param sentimentCalculator: function used to calculate sentiment from a string parameter
    '''
    posReveiwResult = [sentimentCalculator(positiveReview) for positiveReview in positiveReviews]
    negReviewResult = [sentimentCalculator(negativeReview) for negativeReview in negativeReviews]
    return {'results-on-positive':posReveiwResult, 'results-on-negative':negReviewResult}

def runDiagnostics(reviewResult):
    '''
    Print to console the accuracy of the VADER sentiment analyzer
    
    param reviewResult: dictionary containing compound sentiments for positive and negative reviews
    '''
    posReviewResult = reviewResult['results-on-positive']
    negReviewResult = reviewResult['results-on-negative']
    
    truePositive = float(sum(x > 0 for x in posReviewResult))
    trueNegative = float(sum(x < 0 for x in negReviewResult))
    totalAccurate = truePositive + trueNegative

    pctTruePositive = truePositive / len(posReviewResult)
    pctTrueNegative = trueNegative / len(negReviewResult)
    pctAccurate = totalAccurate / (len(posReviewResult) + len(negReviewResult))

    print('Accuracy on positive reviews: {:.2f}%'.format(pctTruePositive*100))
    print('Accuracy on negative reviews: {:.2f}%'.format(pctTrueNegative*100))
    print('Overall accuracy: {:.2f}%'.format(pctAccurate*100))

In [48]:
reviewResult = getReviewSentiments(vaderSentiment)
runDiagnostics(reviewResult)

Accuracy on positive reviews: 69.44%
Accuracy on negative reviews: 40.09%
Overall accuracy: 54.76%


In [54]:
'''
#############################################################
 Test Sentiwordnet's sentiment analyzer with a movie reviews
#############################################################
'''

# test out sentiwordnet
from nltk.corpus import sentiwordnet as swn
for syn in list(swn.senti_synsets('dog')):
    print(syn)
    print(syn.pos_score())
    print(syn.neg_score())

<dog.n.01: PosScore=0.0 NegScore=0.0>
0.0
0.0
<frump.n.01: PosScore=0.0 NegScore=0.5>
0.0
0.5
<dog.n.03: PosScore=0.0 NegScore=0.0>
0.0
0.0
<cad.n.01: PosScore=0.0 NegScore=1.0>
0.0
1.0
<frank.n.02: PosScore=0.0 NegScore=0.0>
0.0
0.0
<pawl.n.01: PosScore=0.0 NegScore=0.0>
0.0
0.0
<andiron.n.01: PosScore=0.0 NegScore=0.0>
0.0
0.0
<chase.v.01: PosScore=0.0 NegScore=0.0>
0.0
0.0


In [78]:
def superNaiveSentiment(review):
    '''
    Most naive sentiment analyzer that utilizes a wordnet. 
    Assumes all words used take on their most common meaning.
    '''
    reviewPolarity = 0.0
    numExceptions = 0
    for word in review.lower().split():
        weight = 0.0
        try:
            synset = list(swn.senti_synsets(word))
            common_meaning = synset[0] # assume first meaning (most common) is the correct one
            if common_meaning.pos_score() > common_meaning.neg_score():
                weight = weight + common_meaning.pos_score()
            elif common_meaning.pos_score() < common_meaning.neg_score():
                weight = weight - common_meaning.neg_score()
        except:
            numExceptions = numExceptions + 1
        #print("Word: {0}\tWeight: {1}".format(word, weight))
        
        reviewPolarity = reviewPolarity + weight

    return reviewPolarity


In [79]:
runDiagnostics(getReviewSentiments(superNaiveSentiment))

Word: the	Weight: 0.0
Word: rock	Weight: 0.0
Word: is	Weight: 0.25
Word: destined	Weight: 0.0
Word: to	Weight: 0.0
Word: be	Weight: 0.0
Word: the	Weight: 0.0
Word: 21st	Weight: 0.0
Word: century's	Weight: 0.0
Word: new	Weight: 0.375
Word: "	Weight: 0.0
Word: conan	Weight: 0.0
Word: "	Weight: 0.0
Word: and	Weight: 0.0
Word: that	Weight: 0.0
Word: he's	Weight: 0.0
Word: going	Weight: 0.0
Word: to	Weight: 0.0
Word: make	Weight: 0.5
Word: a	Weight: 0.0
Word: splash	Weight: 0.0
Word: even	Weight: 0.0
Word: greater	Weight: 0.5
Word: than	Weight: 0.0
Word: arnold	Weight: 0.0
Word: schwarzenegger	Weight: 0.0
Word: ,	Weight: 0.0
Word: jean-claud	Weight: 0.0
Word: van	Weight: 0.0
Word: damme	Weight: 0.0
Word: or	Weight: 0.0
Word: steven	Weight: 0.0
Word: segal	Weight: 0.0
Word: .	Weight: 0.0
Word: the	Weight: 0.0
Word: gorgeously	Weight: 0.5
Word: elaborate	Weight: 0.0
Word: continuation	Weight: 0.0
Word: of	Weight: 0.0
Word: "	Weight: 0.0
Word: the	Weight: 0.0
Word: lord	Weight: 0.0
Word: of	We

Word: movie	Weight: 0.0
Word: a	Weight: 0.0
Word: great	Weight: 0.0
Word: yarn	Weight: 0.0
Word: .	Weight: 0.0
Word: 'compleja	Weight: 0.0
Word: e	Weight: 0.375
Word: intelectualmente	Weight: 0.0
Word: retadora	Weight: 0.0
Word: ,	Weight: 0.0
Word: el	Weight: 0.0
Word: ladrón	Weight: 0.0
Word: de	Weight: 0.0
Word: orquídeas	Weight: 0.0
Word: es	Weight: 0.0
Word: uno	Weight: 0.0
Word: de	Weight: 0.0
Word: esos	Weight: 0.0
Word: filmes	Weight: 0.0
Word: que	Weight: 0.0
Word: vale	Weight: 0.0
Word: la	Weight: 0.0
Word: pena	Weight: 0.0
Word: ver	Weight: 0.0
Word: precisamente	Weight: 0.0
Word: por	Weight: 0.0
Word: su	Weight: 0.0
Word: originalidad	Weight: 0.0
Word: .	Weight: 0.0
Word: '	Weight: 0.0
Word: the	Weight: 0.0
Word: film	Weight: 0.0
Word: makes	Weight: 0.5
Word: a	Weight: 0.0
Word: strong	Weight: 0.5
Word: case	Weight: 0.0
Word: for	Weight: 0.0
Word: the	Weight: 0.0
Word: importance	Weight: 0.75
Word: of	Weight: 0.0
Word: the	Weight: 0.0
Word: musicians	Weight: 0.0
Word: in	Wei

Word: out	Weight: 0.0
Word: the	Weight: 0.0
Word: real	Weight: 0.0
Word: world	Weight: 0.0
Word: ,	Weight: 0.0
Word: and	Weight: 0.0
Word: take	Weight: 0.0
Word: a	Weight: 0.0
Word: vicarious	Weight: -0.375
Word: voyage	Weight: 0.0
Word: to	Weight: 0.0
Word: the	Weight: 0.0
Word: last	Weight: 0.0
Word: frontier	Weight: 0.0
Word: --	Weight: 0.0
Word: space	Weight: 0.0
Word: .	Weight: 0.0
Word: merely	Weight: 0.0
Word: as	Weight: 0.0
Word: a	Weight: 0.0
Word: technical	Weight: 0.0
Word: ,	Weight: 0.0
Word: logistical	Weight: 0.0
Word: feat	Weight: 0.375
Word: ,	Weight: 0.0
Word: russian	Weight: 0.0
Word: ark	Weight: 0.0
Word: marks	Weight: 0.0
Word: a	Weight: 0.0
Word: cinematic	Weight: 0.0
Word: milestone	Weight: 0.0
Word: .	Weight: 0.0
Word: [schweiger	Weight: 0.0
Word: is]	Weight: 0.0
Word: talented	Weight: 0.5
Word: and	Weight: 0.0
Word: terribly	Weight: 0.25
Word: charismatic	Weight: 0.5
Word: ,	Weight: 0.0
Word: qualities	Weight: 0.375
Word: essential	Weight: -0.125
Word: to	Weight

Word: mr	Weight: 0.0
Word: .	Weight: 0.0
Word: parker	Weight: 0.0
Word: has	Weight: 0.0
Word: brilliantly	Weight: 0.375
Word: updated	Weight: 0.0
Word: his	Weight: 0.0
Word: source	Weight: 0.0
Word: and	Weight: 0.0
Word: grasped	Weight: 0.125
Word: its	Weight: 0.0
Word: essence	Weight: 0.25
Word: ,	Weight: 0.0
Word: composing	Weight: 0.0
Word: a	Weight: 0.0
Word: sorrowful	Weight: -0.75
Word: and	Weight: 0.0
Word: hilarious	Weight: -0.5
Word: tone	Weight: -0.125
Word: poem	Weight: 0.0
Word: about	Weight: 0.0
Word: alienated	Weight: 0.5
Word: labor	Weight: 0.0
Word: ,	Weight: 0.0
Word: or	Weight: 0.0
Word: an	Weight: -0.125
Word: absurdist	Weight: 0.0
Word: workplace	Weight: 0.0
Word: sitcom	Weight: 0.0
Word: .	Weight: 0.0
Word: the	Weight: 0.0
Word: result	Weight: 0.0
Word: is	Weight: 0.25
Word: something	Weight: 0.0
Word: quite	Weight: -0.625
Word: fresh	Weight: -0.625
Word: and	Weight: 0.0
Word: delightful	Weight: 0.75
Word: .	Weight: 0.0
Word: all	Weight: 0.0
Word: but	Weight: 0.0
W

Word: of	Weight: 0.0
Word: david	Weight: 0.0
Word: mamet	Weight: 0.0
Word: and	Weight: 0.0
Word: is	Weight: 0.25
Word: enormous	Weight: 0.0
Word: fun	Weight: 0.375
Word: for	Weight: 0.0
Word: thinking	Weight: 0.125
Word: audiences	Weight: 0.0
Word: .	Weight: 0.0
Word: it's	Weight: 0.0
Word: one	Weight: 0.0
Word: of	Weight: 0.0
Word: the	Weight: 0.0
Word: saddest	Weight: -0.75
Word: films	Weight: 0.0
Word: i	Weight: 0.0
Word: have	Weight: 0.0
Word: ever	Weight: 0.0
Word: seen	Weight: 0.0
Word: that	Weight: 0.0
Word: still	Weight: 0.0
Word: manages	Weight: 0.125
Word: to	Weight: 0.0
Word: be	Weight: 0.0
Word: uplifting	Weight: 0.0
Word: but	Weight: 0.0
Word: not	Weight: -0.625
Word: overly	Weight: -0.25
Word: sentimental	Weight: 0.625
Word: .	Weight: 0.0
Word: morton	Weight: 0.0
Word: is	Weight: 0.25
Word: ,	Weight: 0.0
Word: as	Weight: 0.0
Word: usual	Weight: 0.125
Word: ,	Weight: 0.0
Word: brilliant	Weight: 0.875
Word: .	Weight: 0.0
Word: even	Weight: 0.0
Word: with	Weight: 0.0
Word: a

...

Word: a	Weight: 0.0
Word: movie	Weight: 0.0
Word: to	Weight: 0.0
Word: avoid	Weight: 0.0
Word: solving	Weight: 0.0
Word: one	Weight: 0.0
Word: problem	Weight: -0.625
Word: by	Weight: 0.0
Word: trying	Weight: 0.0
Word: to	Weight: 0.0
Word: distract	Weight: 0.0
Word: us	Weight: 0.0
Word: with	Weight: 0.0
Word: the	Weight: 0.0
Word: solution	Weight: 0.0
Word: to	Weight: 0.0
Word: another	Weight: -0.125
Word: .	Weight: 0.0
Word: the	Weight: 0.0
Word: movie	Weight: 0.0
Word: is	Weight: 0.25
Word: genial	Weight: 0.625
Word: but	Weight: 0.0
Word: never	Weight: -0.625
Word: inspired	Weight: 0.125
Word: ,	Weight: 0.0
Word: and	Weight: 0.0
Word: little	Weight: -0.25
Word: about	Weight: 0.0
Word: it	Weight: 0.0
Word: will	Weight: 0.125
Word: stay	Weight: 0.0
Word: with	Weight: 0.0
Word: you	Weight: 0.0
Word: .	Weight: 0.0
Word: the	Weight: 0.0
Word: movie	Weight: 0.0
Word: obviously	Weight: 0.5
Word: seeks	Weight: 0.0
Word: to	Weight: 0.0
Word: re-create	Weight: 0.0
Word: the	Weight: 0.0
Word: ex

Word: inclination	Weight: 0.375
Word: to	Weight: 0.0
Word: provide	Weight: 0.0
Word: a	Weight: 0.0
Word: fourth	Weight: 0.0
Word: book	Weight: 0.0
Word: .	Weight: 0.0
Word: death	Weight: 0.0
Word: to	Weight: 0.0
Word: smoochy	Weight: 0.0
Word: tells	Weight: 0.0
Word: a	Weight: 0.0
Word: moldy-oldie	Weight: 0.0
Word: ,	Weight: 0.0
Word: not-nearly	Weight: 0.0
Word: -as-nasty	Weight: 0.0
Word: -as-it-	Weight: 0.0
Word: thinks-it-is	Weight: 0.0
Word: joke	Weight: 0.375
Word: .	Weight: 0.0
Word: over	Weight: 0.0
Word: and	Weight: 0.0
Word: over	Weight: 0.0
Word: again	Weight: 0.0
Word: .	Weight: 0.0
Word: the	Weight: 0.0
Word: threat	Weight: 0.0
Word: implied	Weight: -0.125
Word: in	Weight: 0.0
Word: the	Weight: 0.0
Word: title	Weight: 0.0
Word: pokémon	Weight: 0.0
Word: 4ever	Weight: 0.0
Word: is	Weight: 0.25
Word: terrifying	Weight: 0.25
Word: –	Weight: 0.0
Word: like	Weight: 0.125
Word: locusts	Weight: 0.0
Word: in	Weight: 0.0
Word: a	Weight: 0.0
Word: horde	Weight: 0.0
Word: these	Weig

Word: rejected	Weight: 0.0
Word: x-files	Weight: 0.0
Word: episode	Weight: 0.0
Word: than	Weight: 0.0
Word: a	Weight: 0.0
Word: credible	Weight: 0.625
Word: account	Weight: 0.0
Word: of	Weight: 0.0
Word: a	Weight: 0.0
Word: puzzling	Weight: -0.25
Word: real-life	Weight: 0.0
Word: happening	Weight: 0.0
Word: .	Weight: 0.0
Word: some	Weight: 0.0
Word: motion	Weight: 0.0
Word: pictures	Weight: 0.0
Word: portray	Weight: 0.0
Word: ultimate	Weight: 0.0
Word: passion	Weight: 0.5
Word: ;	Weight: 0.0
Word: others	Weight: 0.0
Word: create	Weight: 0.0
Word: ultimate	Weight: 0.0
Word: thrills	Weight: 0.0
Word: .	Weight: 0.0
Word: men	Weight: 0.0
Word: in	Weight: 0.0
Word: black	Weight: -0.375
Word: ii	Weight: 0.0
Word: achieves	Weight: 0.0
Word: ultimate	Weight: 0.0
Word: insignificance	Weight: 0.375
Word: --	Weight: 0.0
Word: it's	Weight: 0.0
Word: the	Weight: 0.0
Word: sci-fi	Weight: 0.0
Word: comedy	Weight: 0.0
Word: spectacle	Weight: 0.125
Word: as	Weight: 0.0
Word: whiffle-ball	Weight: 0.0
Wo

Word: amélie	Weight: 0.0
Word: .	Weight: 0.0
Word: overburdened	Weight: 0.0
Word: with	Weight: 0.0
Word: complicated	Weight: -0.125
Word: plotting	Weight: 0.0
Word: and	Weight: 0.0
Word: banal	Weight: -0.375
Word: dialogue	Weight: 0.25
Word: ensemble	Weight: 0.0
Word: movies	Weight: 0.0
Word: ,	Weight: 0.0
Word: like	Weight: 0.125
Word: soap	Weight: 0.0
Word: operas	Weight: 0.0
Word: ,	Weight: 0.0
Word: depend	Weight: 0.0
Word: on	Weight: 0.0
Word: empathy	Weight: -0.25
Word: .	Weight: 0.0
Word: if	Weight: 0.0
Word: there	Weight: 0.0
Word: ain't	Weight: 0.0
Word: none	Weight: 0.0
Word: ,	Weight: 0.0
Word: you	Weight: 0.0
Word: have	Weight: 0.0
Word: a	Weight: 0.0
Word: problem	Weight: -0.625
Word: .	Weight: 0.0
Word: the	Weight: 0.0
Word: master	Weight: 0.625
Word: of	Weight: 0.0
Word: disguise	Weight: 0.375
Word: falls	Weight: 0.0
Word: under	Weight: 0.0
Word: the	Weight: 0.0
Word: category	Weight: 0.0
Word: of	Weight: 0.0
Word: 'should	Weight: 0.0
Word: have	Weight: 0.0
Word: been	We

Word: grenade	Weight: 0.0
Word: with	Weight: 0.0
Word: his	Weight: 0.0
Word: teeth	Weight: 0.0
Word: ,	Weight: 0.0
Word: windtalkers	Weight: 0.0
Word: seems	Weight: 0.0
Word: to	Weight: 0.0
Word: have	Weight: 0.0
Word: ransacked	Weight: 0.0
Word: every	Weight: 0.0
Word: old	Weight: 0.0
Word: world	Weight: 0.0
Word: war	Weight: 0.0
Word: ii	Weight: 0.0
Word: movie	Weight: 0.0
Word: for	Weight: 0.0
Word: overly	Weight: -0.25
Word: familiar	Weight: 0.0
Word: material	Weight: 0.0
Word: .	Weight: 0.0
Word: if	Weight: 0.0
Word: a	Weight: 0.0
Word: few	Weight: 0.0
Word: good	Weight: 0.5
Word: men	Weight: 0.0
Word: told	Weight: 0.0
Word: us	Weight: 0.0
Word: that	Weight: 0.0
Word: we	Weight: 0.0
Word: "	Weight: 0.0
Word: can't	Weight: 0.0
Word: handle	Weight: 0.0
Word: the	Weight: 0.0
Word: truth	Weight: 0.625
Word: "	Weight: 0.0
Word: than	Weight: 0.0
Word: high	Weight: 0.125
Word: crimes	Weight: 0.0
Word: poetically	Weight: 0.25
Word: states	Weight: 0.0
Word: at	Weight: 0.0
Word: one	Weight:

In [83]:
from string import punctuation 
from nltk.corpus import stopwords
stopwords = set(stopwords.words('english') + list(punctuation))
# !CAVEAT!  stopwords includes the word 'not'

def naiveSentiment(review):
    '''
    Naive sentiment analyzer that utilizes a wordnet. 
    Uses avg polarity of meanings for each word as the weight
    Removes stopwords, even those associated with negation
    '''
    reviewPolarity = 0.0
    numExceptions = 0
    for word in review.lower().split():
        if word in stopwords:
            continue
        numMeanings = 0
        weight = 0.0
        try:
            for meaning in list(swn.senti_synsets(word)):
                if meaning.pos_score() != meaning.neg_score():
                    weight = weight + (meaning.pos_score() - meaning.neg_score())
                    numMeanings = numMeanings + 1
#                 elif meaning.pos_score() < meaning.neg_score():
#                     weight = weight - (meaning.neg_score() - meaning.neg_score())
#                     num_meanings = num_meanings + 1
        except:
            numExceptions = numExceptions + 1
        #print("Word: {0}\tWeight: {1}".format(word, weight))
        if numMeanings > 0:
            reviewPolarity = reviewPolarity + (weight/numMeanings)

    return reviewPolarity

runDiagnostics(getReviewSentiments(naiveSentiment))


Accuracy on positive reviews: 75.56%
Accuracy on negative reviews: 42.79%
Overall accuracy: 59.17%
